# Data Availability Plot for Streamflow

This notebook is used to explore the streamflow data and its presence in the dataset for 85 basins abailable.

In [1]:
from pathlib import Path

import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.patches as mpatches

In [2]:
sns.set_theme(style="whitegrid")

In [ ]:
output_dir = Path("../output")
start_from = 2000

In [ ]:
streamflow_path = Path("../data/beta_dataset/streamflow")
streamflow_files = sorted(list(streamflow_path.iterdir()), reverse=True)

pdf_streamflow_path = Path("../data/sigma_dataset/streamflow")
pdf_streamflow_files = sorted(list(pdf_streamflow_path.iterdir()), reverse=True)

divergence_path = Path("../data/mismatches")
divergence_files = sorted(list(divergence_path.iterdir()), reverse=True)

In [8]:
web_basins = [x.name for x in streamflow_files]
pdf_basins = [x.name for x in pdf_streamflow_files]
len(web_basins), len(pdf_basins)

(96, 93)

In [9]:
for i in pdf_basins:
    if i not in web_basins:
        print(i)

77895.csv
19013.csv
11242.csv


In [10]:
for i in web_basins:
    if i not in pdf_basins:
        print(i)

19255.csv
13095.csv
11219.csv
11157.csv
11139.csv
11090.csv


In [11]:
basins = pd.read_csv("../ML/basins/basins_sigma_85.txt", header=None)
basins = basins[0].tolist()
basins[:5]

[11001, 11063, 11068, 11077, 11094]

In [12]:
type(basins[0])

int

In [13]:
df = pd.DataFrame(data={"test": [np.nan, np.nan]}, index=[pd.to_datetime(f"{start_from}-01-01"), pd.to_datetime("2022-12-31")])

for i, file in enumerate(streamflow_files):

    _df = pd.read_csv(file, sep=",")
    _df.date = pd.to_datetime(_df.date)
    _df.set_index(["date"], inplace=True)

    basin_id = file.name.split(".")[0]

    if int(basin_id) not in basins:
        print(basin_id)
        continue

    _df.rename(columns={"discharge": basin_id}, inplace=True)
    _df = _df[(_df.index >= f"{start_from}-01-01") & (_df.index <= "2022-12-31")]
    df = pd.concat([df, _df], axis=1)

df = df.asfreq("D", fill_value=np.nan)
del df["test"]

77819
19255
13221
13095
12031
12008
11421
11397
11293
11219
11157
11139
11090


In [14]:
pdf_df = pd.DataFrame(data={"test": [np.nan, np.nan]}, index=[pd.to_datetime(f"{start_from}-01-01"), pd.to_datetime("2022-12-31")])

for i, file in enumerate(pdf_streamflow_files):

    _df = pd.read_csv(file, sep=",")
    _df.date = pd.to_datetime(_df.date)
    _df.set_index(["date"], inplace=True)

    basin_id = file.name.split(".")[0]

    if int(basin_id) not in basins:
        print(basin_id)
        continue

    _df.rename(columns={"discharge": basin_id}, inplace=True)
    _df = _df[(_df.index >= f"{start_from}-01-01") & (_df.index <= "2022-12-31")]
    pdf_df = pd.concat([pdf_df, _df], axis=1)

pdf_df = pdf_df.asfreq("D", fill_value=np.nan)
del pdf_df["test"]

77895
77819
13221
12031
12008
11421
11397
11293


In [15]:
div_df = pd.DataFrame(data={"test": [np.nan, np.nan]}, index=[pd.to_datetime("2008-01-01"), pd.to_datetime("2022-12-31")])

for i, file in enumerate(divergence_files):

    _df = pd.read_csv(file, sep=",")

    if len(_df) == 0:
        continue

    _df.date = pd.to_datetime(_df.date)
    _df.set_index(["date"], inplace=True)

    # basin_id = file.name.split('_')[-1].split(".")[0]
    basin_id = file.name.split(".")[0]

    if int(basin_id) not in basins:
        print(basin_id)
        continue

    _df["divergence"] = 1
    _df = _df[["divergence"]]
    _df.rename(columns={"divergence": basin_id}, inplace=True)

    _df = _df[(_df.index >= f"{start_from}-01-01") & (_df.index <= "2022-12-31")]
    div_df = pd.concat([div_df, _df], axis=1)

div_df = div_df.asfreq("D", fill_value=np.nan)
del div_df["test"]

77819
13221
12008
11397


In [20]:
for col in df.columns:
    if df[col].isnull().all():
        print(col)
        del df[col]

In [21]:
for col in pdf_df.columns:
    if pdf_df[col].isnull().all():
        print(col)
        del pdf_df[col]

In [22]:
all_basins = df.columns.tolist()
all_basins.extend(pdf_df.columns.to_list())
all_basins = sorted(set(all_basins), reverse=True)
len(all_basins)

85

In [23]:
basins_selected = pd.read_csv("../ML/basins/basins_sigma_41.txt", header=None)
basins_selected = basins_selected[0].tolist()
basins_selected = [str(x) for x in basins_selected]
basins_selected = sorted(set(basins_selected), reverse=True)
len(basins_selected)

41

Plot all basins

In [ ]:
from pandas import Timestamp

fig, ax = plt.subplots(figsize=(20, 34), dpi=1200)
y_positions = range(len(all_basins))

fontsize = 20

ax.margins(y=0.0275)
# Set the x-axis limits
start_x = Timestamp('2000-01-01 00:00:00')
end_x = Timestamp('2022-12-31 00:00:00')
ax.set_xlim(start_x, end_x)


website_color = "darkseagreen"
pdf_color = "steelblue"
div_color = "maroon"
selected_color = "orange"

for y, column in zip(y_positions, all_basins):
    if column not in pdf_df.columns:
        continue

    if column in basins_selected:
        # make highlight
        # ax.barh(y, (df[column].index[-1] - df[column].index[0]), left=df[column].index[0], height=0.9, color="palegoldenrod")
        ax.text(pdf_df[column].index[-1] + pd.Timedelta(days=70), y, '✔', color='black', fontweight="bold", fontsize=24, va='center', ha='left')

    idx = 0
    start = None
    for date, value in pdf_df[column].items():
        if not pd.isna(value):
            if start is None:
                start = date
        else:
            if start is not None:
                ax.barh(y, (pdf_df[column].index[idx-1] - start), left=start, height=0.7, color=pdf_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)
                start = None
       
        idx += 1

    if start is not None:
        ax.barh(y, (pdf_df[column].index[-1] - start), left=start, height=0.7, color=pdf_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)


for y, column in zip(y_positions, all_basins):
    if column not in df.columns:
        continue

    idx = 0
    start = None
    for date, value in df[column].items():
        if not pd.isna(value):
            if start is None:
                start = date
        else:
            if start is not None:
                ax.barh(y, (df[column].index[idx-1] - start), left=start, height=0.4, color=website_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)
                start = None
        
        idx += 1

    if start is not None:
        ax.barh(y, (df[column].index[-1] - start), left=start, height=0.4, color=website_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)


for y, column in zip(y_positions, all_basins):
    if column not in div_df.columns:
        continue

    idx = 0
    start = None
    for date, value in div_df[column].items():
        if not pd.isna(value):
            if start is None:
                start = date
        else:
            if start is not None:
                ax.barh(y, (div_df[column].index[idx-1] - start), left=start, height=0.3, color=div_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)
                start = None
        
        idx += 1

    if start is not None:
        ax.barh(y, (div_df[column].index[-1] - start), left=start, height=0.3, color=div_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)


ax.axvline(pd.to_datetime("2008-10-01"), color="darkred")
ax.axvline(pd.to_datetime("2022-12-31"), color="darkred")

handles, labels = ax.get_legend_handles_labels()

data_real = mpatches.Rectangle((0, 0), 1, 0.4, facecolor=website_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)
pdf_data_real = mpatches.Rectangle((0, 0), 1, 0.4, facecolor=pdf_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)
div_data = mpatches.Rectangle((0, 0), 1, 0.4, facecolor=div_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)

# Add these custom bars to the handles and labels
handles += [data_real, pdf_data_real, div_data]
labels += ['Digitized Tabular Data', 'Original PDF Data', 'Regions of Data Divergence']

ax.legend(handles=handles, labels=labels, loc='lower center', ncol=3, prop={'size': fontsize-2, "weight": "bold"})

ax.set_yticks(y_positions)
ax.set_yticklabels(all_basins)
ax.tick_params(axis='both', labelsize=fontsize)
ax.set_xlabel('Timeline', weight="bold", fontsize=fontsize)
ax.set_ylabel('Basin ID', weight="bold", fontsize=fontsize)

plt.savefig(output_dir / f"./streamflow_{len(all_basins)}_{start_from}_new.png", bbox_inches="tight")
plt.close()

In [31]:
fig, ax = plt.subplots(figsize=(20, 34), dpi=1200)
y_positions = range(len(all_basins))

fontsize = 20

fig.subplots_adjust(
    top=0.9,    # space from the top edge
    bottom=0.1, # space from the bottom edge
)

height = 0.4

website_color = "orange"
pdf_color = "steelblue"
div_color = "maroon"
selected_color = ("orange", 0.8)

for y, column in zip(y_positions, all_basins):
    if column not in pdf_df.columns:
        continue

    if column in basins_selected:
        ax.text(pdf_df[column].index[-1] + pd.Timedelta(days=1000), y - 0.15, '✔', color='green', fontweight="bold", fontsize=30, va='center', ha='left')

    idx = 0
    start = None
    for date, value in pdf_df[column].items():
        if not pd.isna(value):
            if start is None:
                start = date
        else:
            if start is not None:
                ax.barh(y - 0.15, (pdf_df[column].index[idx-1] - start), left=start, height=height, color=pdf_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)
                start = None
       
        idx += 1

    if start is not None:
        ax.barh(y - 0.15, (pdf_df[column].index[-1] - start), left=start, height=height, color=pdf_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)


for y, column in zip(y_positions, all_basins):
    if column not in df.columns:
        continue

    idx = 0
    start = None
    for date, value in df[column].items():
        if not pd.isna(value):
            if start is None:
                start = date
        else:
            if start is not None:
                ax.barh(y + 0.15, (df[column].index[idx-1] - start), left=start, height=height, color=website_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)
                start = None
        
        idx += 1

    if start is not None:
        ax.barh(y + 0.15, (df[column].index[-1] - start), left=start, height=height, color=website_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)


for y, column in zip(y_positions, all_basins):
    if column not in div_df.columns:
        continue

    idx = 0
    start = None
    for date, value in div_df[column].items():
        if not pd.isna(value):
            if start is None:
                start = date
        else:
            if start is not None:
                ax.barh(y, (div_df[column].index[idx-1] - start), left=start, height=height, color=div_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)
                start = None
        
        idx += 1

    if start is not None:
        ax.barh(y, (div_df[column].index[-1] - start), left=start, height=height, color=div_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)


ax.axvline(pd.to_datetime("2008-10-01"), color="darkred")
ax.axvline(pd.to_datetime("2022-12-31"), color="darkred")

handles, labels = ax.get_legend_handles_labels()

data_real = mpatches.Rectangle((0, 0), 1, 0.4, facecolor=website_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)
pdf_data_real = mpatches.Rectangle((0, 0), 1, 0.4, facecolor=pdf_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)
div_data = mpatches.Rectangle((0, 0), 1, 0.4, facecolor=(div_color, 0.4), edgecolor=(0, 0, 0, 0.5), linewidth=0.5)
selected_data = mpatches.Rectangle((0, 0), 1, 0.4, facecolor=selected_color, edgecolor=(0, 0, 0, 0.5), linewidth=0.5)

# Add these custom bars to the handles and labels
handles += [data_real, pdf_data_real, div_data]
labels += ['Digitized Tabular Data', 'Original PDF Data', 'Regions of Data Divergence']

ax.legend(handles=handles, labels=labels, loc='lower center', ncol=3, prop={'size': fontsize-2, "weight": "bold"})

ax.set_yticks(y_positions)
ax.set_yticklabels(all_basins)
ax.tick_params(axis='both', labelsize=fontsize)
ax.set_xlabel('Timeline', weight="bold", fontsize=fontsize)
ax.set_ylabel('Basin ID', weight="bold", fontsize=fontsize)

plt.savefig(output_dir / f"./streamflow_{len(all_basins)}_{start_from}_new.svg", bbox_inches="tight")
# plt.savefig(output_dir / f"./streamflow_{len(all_basins)}_{start_from}.png", bbox_inches="tight")
# plt.show()